## Bias Correction on hydrological model output

Basin: Santa Lucia \
Hydrological model: WFLOW-SBM \
Timestep: Daily \
Station: 133.0 Santa Lucia

#### Import libraries

In [20]:
import math
import requests
import geoglows
import numpy as np
import pandas as pd
import datetime as dt
import geopandas as gpd
import hydrostats as hs
import scipy.stats as sp
import plotly.express as px
import hydrostats.data as hd
import plotly.graph_objs as go

from IPython.display import display, HTML

import warnings
warnings.filterwarnings('ignore')

#### Define files names and location

In [21]:
obs_file = 'data/qobs.csv'
sim_file = 'data/qsim.csv'

#### import observed historical data

In [22]:
observed_historical = pd.read_csv(obs_file, parse_dates=['Fecha'],index_col="Fecha",dayfirst=True,na_values="NA")
observed_historical.index = pd.to_datetime(observed_historical.index)
observed_historical.index = observed_historical.index.to_series().dt.strftime("%Y-%m-%d")
observed_historical.index = pd.to_datetime(observed_historical.index)
# reindex de missing data
# Identify the missing data from a date range (1980 to 2023)
observed_missing = pd.date_range(start = observed_historical.index[0].strftime('%Y-%m-%d'), end = observed_historical.index[-1].strftime('%Y-%m-%d'),freq='D')
# Re-index the dataframe based on the missind date variable
observed_historical = observed_historical.reindex(observed_missing,fill_value=None)
observed_historical.index.name = 'time'
observed_historical.rename(columns={observed_historical.columns[0]: "qobs"}, inplace=True)
display(HTML(observed_historical.tail(6).to_html()))

#### import simulated historical data

In [23]:
# Cargar el archivo y convertir la columna 'time' a DatetimeIndex
simulated_historical = pd.read_csv(sim_file, parse_dates=['time'], index_col='time')
simulated_historical.index = simulated_historical.index.strftime('%Y-%m-%d')
simulated_historical.index = pd.to_datetime(simulated_historical.index)
simulated_historical.rename(columns={simulated_historical.columns[0]: "qsim"}, inplace=True)
display(HTML(simulated_historical.tail(6).to_html()))

#### Define period for calculating bias-correction

In [24]:
# Here we select the period of record to create the monthly Flow Duration Curve (FDC)
tstart = "2011-01-01"
tend = "2019-12-31"

In [25]:
# Filter data between the tstart and tend
filtered_observed = observed_historical.loc[tstart:tend]
filtered_simulated = simulated_historical.loc[tstart:tend]
# define datetime in the string date column
filtered_observed.index = pd.to_datetime(filtered_observed.index)
filtered_simulated.index = pd.to_datetime(filtered_simulated.index)

#### Performing Bias-Correction

Here we are going to apply the correct_historical function provided by the GeoGlows Package

In [26]:

corrected_historical = geoglows.bias.correct_historical(filtered_simulated, filtered_observed)
corrected_historical.index = pd.to_datetime(corrected_historical.index)
corrected_historical.index = corrected_historical.index.to_series().dt.strftime("%Y-%m-%d")
corrected_historical.index = pd.to_datetime(corrected_historical.index)
display(HTML(corrected_historical.tail(6).to_html()))

#### Plotting the results

In [27]:
site = 'Santa Lucia River at Ruta 11 (station id = 133.0)'
plot_titles = [f' Santa Lucia River at Ruta 11 (station id = 133.0)']
# This is a plot of the Original Simulated, Corrected Simulated, and Observed data
hydroviewer_figure = geoglows.plots.corrected_retrospective(corrected_historical, filtered_simulated, filtered_observed, plot_titles=plot_titles)
hydroviewer_figure.show()

In [28]:
#Scatter Plot in Normal Scale
'''Merge Data'''

merged_df = hd.merge_data(sim_df=filtered_simulated, obs_df=filtered_observed)
merged_df2 = hd.merge_data(sim_df=corrected_historical, obs_df=filtered_observed)

'''Plotting Data'''

scatter_data = go.Scatter(
    x=merged_df.iloc[:, 0].values,
		y=merged_df.iloc[:, 1].values,
		mode='markers',
		name='original',
		marker=dict(color='#ef553b')
)

scatter_data2 = go.Scatter(
    x=merged_df2.iloc[:, 0].values,
		y=merged_df2.iloc[:, 1].values,
		mode='markers',
		name='corrected',
		marker=dict(color='#00cc96')
)

min_value = min(min(merged_df.iloc[:, 1].values), min(merged_df.iloc[:, 0].values))
max_value = max(max(merged_df.iloc[:, 1].values), max(merged_df.iloc[:, 0].values))

min_value2 = min(min(merged_df2.iloc[:, 1].values), min(merged_df2.iloc[:, 0].values))
max_value2 = max(max(merged_df2.iloc[:, 1].values), max(merged_df2.iloc[:, 0].values))

line_45 = go.Scatter(
    x=[min_value, max_value],
		y=[min_value, max_value],
		mode='lines',
		name='45deg line',
		line=dict(color='black')
)

slope, intercept, r_value, p_value, std_err = sp.linregress(merged_df.iloc[:, 0].values, merged_df.iloc[:, 1].values)

slope2, intercept2, r_value2, p_value2, std_err2 = sp.linregress(merged_df2.iloc[:, 0].values, merged_df2.iloc[:, 1].values)

line_adjusted = go.Scatter(
    x=[min_value, max_value],
		y=[slope * min_value + intercept, slope * max_value + intercept],
		mode='lines',
		name='{0}x + {1} (Original)'.format(str(round(slope, 2)), str(round(intercept, 2))),
		line=dict(color='red')
)

line_adjusted2 = go.Scatter(
    x=[min_value, max_value],
		y=[slope2 * min_value + intercept2, slope2 * max_value + intercept2],
		mode='lines',
		name='{0}x + {1} (Corrected)'.format(str(round(slope2, 2)), str(round(intercept2, 2))),
		line=dict(color='green')
)

layout = go.Layout(title="Scatter Plot for {0} - {1}".format(site, "133.0"),
                   xaxis=dict(title='Simulated', ), yaxis=dict(title='Observed', autorange=True),
                   showlegend=True)

chart_obj = go.Figure(data=[scatter_data, scatter_data2, line_45, line_adjusted, line_adjusted2], layout=layout)

chart_obj.show()

In [29]:
# This is a plot of the daily averages
hydroviewer_figure = geoglows.plots.corrected_day_average(corrected_historical, filtered_simulated, filtered_observed, plot_titles=plot_titles)
hydroviewer_figure.show()

In [30]:
# This is a plot of the monthly averages
hydroviewer_figure =  geoglows.plots.corrected_month_average(corrected_historical, filtered_simulated, filtered_observed, plot_titles=plot_titles)
hydroviewer_figure.show()

In [31]:
display(HTML(geoglows.bias.statistics_tables(corrected_historical, filtered_simulated, filtered_observed)))

In [32]:
def plot_fdc(*dataframes, labels=None):
    """
    It generates a Flow Duration Curve for different Dataframe.
    
    Parameters:
    - *dataframes: one or more dataframe with DatetimeIndex and one column (streamflow)
    - labels (list, optional): list with labels
    
    Return:
    - Graphic with the FDC with log-scale 
    """
    fig = go.Figure()

    if labels is None:
        labels = [f"Serie {i+1}" for i in range(len(dataframes))]

    for i, df in enumerate(dataframes):
        # Make sur to use DatetimeIndex
        df.index = pd.to_datetime(df.index)

        # Extrat daily discharge 
        q_daily = df.iloc[:, 0].dropna()

        # Sort discharge from highest to lowest
        q_sorted = q_daily.sort_values(ascending=False).reset_index(drop=True)

        # Calculate the Probability of excedeence 
        n = len(q_sorted)
        exceedance_prob = [(j + 1) / (n + 1) * 100 for j in range(n)]

        # Add into the graph
        fig.add_trace(go.Scatter(
            x=exceedance_prob, 
            y=q_sorted,
            mode='lines',
            name=labels[i]
        ))

    # update graph (log scale in Y)
    fig.update_layout(
        title="Flow Duration Curve",
        xaxis_title="Non-exceedance Probability (%)",
        yaxis_title="Streamflow (m³/s)",
        xaxis=dict(type='linear', autorange=True),  # X linear scale
        yaxis=dict(type='log', tickformat=".2f"),  # Y log scale and no scientific notation
        legend_title="FDC"
    )

    return fig


In [33]:
fig = plot_fdc(corrected_historical, filtered_simulated, filtered_observed, labels=["Qbc", "Qsim", "Qobs"])
fig.show()


#### Bias-correct global forecast model

The GEOGLOWS Streamflow Forecasting initiative leverages advanced hydrological models and high-resolution global meteorological data to provide accurate, real-time forecasts of river discharge for millions of stream segments worldwide. The system's improved data services, enhanced visualization tools, and robust analytical capabilities enable users to access, analyze, and apply streamflow data efficiently for a wide range of applications, from flood management and early warning systems to water resource planning. With continuous updates and community engagement, GEOGLOWS ensures that its forecasting services remain at the forefront of hydrological science and technology

You can access the forecast in the following page https://hydroviewer.geoglows.org/#lon=10.00&lat=18.00&zoom=3.00&definition= 

Example of usage:
```python
historical_data = geoglows.data.retrospective(river_id=640184248)
```

In our case, we already know the reach ID of the stream we are working with. For the hydrological station on the Santa Lucia River called SANTA LUCIA RUTA 11, the corresponding `reach_id` is 640184248.

In [34]:
# Edit the comid with the reach ID of your stream
comid = 640184248
print(f"COMID: {comid}")

COMID: 640184248


In [35]:
# Obtain simulation from GeoGlows
sim_geoglows = geoglows.data.retrospective(comid)
sim_geoglows.index = pd.to_datetime(sim_geoglows.index)
sim_geoglows[sim_geoglows < 0] = 0
sim_geoglows.index = sim_geoglows.index.to_series().dt.strftime("%Y-%m-%d")
sim_geoglows.index = pd.to_datetime(sim_geoglows.index)

display(HTML(sim_geoglows.tail(6).to_html()))

In [38]:
# Here we select the period of record to create the monthly Flow Duration Curve (FDC)
tstart = "1980-01-01"
tend = "2024-12-31"

# Filter data between the tstart and tend
filtered_observed = observed_historical.loc[tstart:tend]
filtered_simulated = simulated_historical.loc[tstart:tend]
# define datetime in the string date column
filtered_observed.index = pd.to_datetime(filtered_observed.index)

In [39]:
corrected_geoglows = geoglows.bias.correct_historical(sim_geoglows, filtered_observed)
corrected_geoglows.index = pd.to_datetime(corrected_geoglows.index)
corrected_geoglows.index = corrected_geoglows.index.to_series().dt.strftime("%Y-%m-%d")
corrected_geoglows.index = pd.to_datetime(corrected_geoglows.index)

display(HTML(corrected_geoglows.tail(6).to_html()))

In [40]:
site = 'Santa Lucia River @ Santa Lucia R-11 (station id = 133.0)'
plot_titles = [f'. Site: {site}', f'Reach ID: {comid}']

# This is a plot of the Original Simulated, Corrected Simulated, and Observed data
hydroviewer_figure = geoglows.plots.corrected_retrospective(corrected_geoglows, sim_geoglows, filtered_observed, plot_titles=plot_titles)
hydroviewer_figure.show()

In [41]:
# This is a plot of the monthly averages
hydroviewer_figure =  geoglows.plots.corrected_month_average(corrected_geoglows, sim_geoglows, filtered_observed, plot_titles=plot_titles)
hydroviewer_figure.show()

Calculate differente metrics for the simulated historical GeoGlows and the corrected simulation 

In [43]:
'''Merge Data'''

merged_df = hd.merge_data(sim_df=sim_geoglows, obs_df=filtered_observed)
merged_df2 = hd.merge_data(sim_df=corrected_geoglows, obs_df=filtered_observed)

''' Calculate metrics '''

metrics = ['ME', 'RMSE', 'NRMSE (Mean)', 'MAPE', 'NSE', 'KGE (2009)', 'KGE (2012)', "R (Pearson)", "R (Spearman)", "r2"]
# Merge Data
table1 = hs.make_table(merged_dataframe=merged_df, metrics=metrics)
table2 = hs.make_table(merged_dataframe=merged_df2, metrics=metrics)

table2 = table2.rename(index={'Full Time Series': 'Corrected Full Time Series'})
table1 = table1.rename(index={'Full Time Series': 'Original Full Time Series'})
table1 = table1.transpose()
table2 = table2.transpose()

table_final = pd.merge(table1, table2, right_index=True, left_index=True)

display(HTML(table_final.to_html()))
